<a href="https://colab.research.google.com/github/DEP04929/ESICMDatathon2026/blob/main/ExploringData_20260111.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Pre-requisites for Amsterdam UMC DB


In [1]:
# sets *your* project id
PROJECT_ID = "esicmdatathon2026" #@param {type:"string"}


In [2]:
# sets default dataset for AmsterdamUMCdb
DATASET_PROJECT_ID = 'amsterdamumcdb' #@param {type:"string"}
DATASET_ID = 'van_gogh_2026_datathon' #@param {type:"string"}
LOCATION = 'eu' #@param {type:"string"}

In [3]:
import os
from google.colab import auth

# all libraries check this environment variable, so set it:
os.environ["GOOGLE_CLOUD_PROJECT"] = PROJECT_ID

auth.authenticate_user()
print('Authenticated')


Authenticated


In [4]:
%load_ext google.colab.data_table
from google.colab.data_table import DataTable

# change default limits:
DataTable.max_columns = 50
DataTable.max_rows = 30000


In [5]:
from google.cloud.bigquery import magics
from google.cloud import bigquery

# sets the default query job configuration
def_config = bigquery.job.QueryJobConfig(default_dataset=DATASET_PROJECT_ID + "." + DATASET_ID)
magics.context.default_query_job_config = def_config


In [6]:
import pandas as pd
import numpy as np

import matplotlib as plt
import seaborn as sns
sns.set_style('darkgrid')

# Exploring data
Am trying to follow :
https://github.com/AmsterdamUMC/AmsterdamUMCdb/blob/master/omop/sql/ddl/bigquery.sql

Ventilator modes appear to be missing. Not possible to find specifics like HFOV for example.

In [201]:
%%bigquery test --project esicmdatathon2026
select person_id, measurement_date, value_as_number, measurement_source_value
from measurement
where measurement_concept_id in (3004921 -- Ventilation mode Ventilator
)
  and person_id = 51316 -- testing purpose only

Query is running:   0%|          |

Downloading:   0%|          |

In [202]:
test


person_id measurement_date  value_as_number  \
0        51316       2017-06-24              NaN   
1        51316       2017-06-24              NaN   
2        51316       2017-06-24              NaN   
3        51316       2017-06-24              NaN   
4        51316       2017-06-24              NaN   
..         ...              ...              ...   
142      51316       2017-06-24              NaN   
143      51316       2017-06-24              NaN   
144      51316       2017-06-24              NaN   
145      51316       2017-06-24              NaN   
146      51316       2017-06-24              NaN   

                      measurement_source_value  
0    Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
1    Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
2    Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
3    Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
4    Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
..                                         ...  
142  Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
143  Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
144  Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
145  Beademingsmodus;R UMCA AN BEADEMINGSMODUS  
146  Beademingsmodus;R UMCA AN BEADEMINGSMODUS  

[147 rows x 4 columns]

Diagnosis is now condition, and without concepts. Just text based searching.

In [203]:
%%bigquery test --project esicmdatathon2026
select *
from condition_occurrence
where person_id = 51316 -- 43138

Query is running:   0%|          |

Downloading:   0%|          |

In [204]:
test


person_id  condition_concept_id condition_start_date  \
0      51316                     0           2017-01-01   
1      51316                     0           2017-01-01   
2      51316                     0           2017-01-23   

   condition_start_datetime condition_end_date condition_end_datetime  \
0 2017-01-01 02:00:00+00:00                NaT                    NaT   
1 2017-01-01 02:00:00+00:00                NaT                    NaT   
2 2017-01-23 16:15:00+00:00                NaT                    NaT   

   condition_type_concept_id  \
0                      32879   
1                      32879   
2                      32879   

                              condition_source_value  
0  Subarachnoid hemorrhage/intracranial aneurysm,...  
1  Coma/change in level of consciousness (for hep...  
2      Subarachnoid hemorrhage/intracranial aneurysm

It is possible to see modes of non-invasive ventilation

In [205]:
%%bigquery test --project esicmdatathon2026
select * --person_id, measurement_date, measurement_datetime, value_as_number, value_source_value, measurement_source_value
from measurement
where measurement_concept_id in (2000000250 -- Ventilation mode Ventilator non-invasive
)
  and person_id = 49440 -- testing purpose only
limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [206]:
test

person_id  measurement_concept_id measurement_date  \
0       49440              2000000250       2002-01-22   
1       49440              2000000250       2002-01-23   
2       49440              2000000250       2002-01-23   
3       49440              2000000250       2002-01-23   
4       49440              2000000250       2002-01-23   
5       49440              2000000250       2002-01-22   
6       49440              2000000250       2002-01-23   
7       49440              2000000250       2002-01-23   
8       49440              2000000250       2002-01-22   
9       49440              2000000250       2002-01-22   
10      49440              2000000250       2002-01-23   
11      49440              2000000250       2002-01-22   
12      49440              2000000250       2002-01-22   

        measurement_datetime  measurement_type_concept_id  value_as_number  \
0  2002-01-22 21:11:00+00:00                            0              5.0   
1  2002-01-23 10:11:00+00:00                            0              5.0   
2  2002-01-23 09:11:00+00:00                            0              5.0   
3  2002-01-23 13:11:00+00:00                            0              5.0   
4  2002-01-23 12:11:00+00:00                            0              5.0   
5  2002-01-22 23:11:00+00:00                            0              5.0   
6  2002-01-23 05:11:00+00:00                            0              5.0   
7  2002-01-23 01:11:00+00:00                            0              5.0   
8  2002-01-22 19:11:00+00:00                            0              5.0   
9  2002-01-22 20:11:00+00:00                            0              5.0   
10 2002-01-23 11:11:00+00:00                            0              5.0   
11 2002-01-22 18:11:00+00:00                            0              8.0   
12 2002-01-22 17:11:00+00:00                            0              8.0   

   measurement_source_value unit_source_value value_source_value  
0       CPAP (Bipap Vision)             cmH2O                5.0  
1       CPAP (Bipap Vision)             cmH2O                5.0  
2       CPAP (Bipap Vision)             cmH2O                5.0  
3       CPAP (Bipap Vision)             cmH2O                5.0  
4       CPAP (Bipap Vision)             cmH2O                5.0  
5       CPAP (Bipap Vision)             cmH2O                5.0  
6       CPAP (Bipap Vision)             cmH2O                5.0  
7       CPAP (Bipap Vision)             cmH2O                5.0  
8       CPAP (Bipap Vision)             cmH2O                5.0  
9       CPAP (Bipap Vision)             cmH2O                5.0  
10      CPAP (Bipap Vision)             cmH2O                5.0  
11      CPAP (Bipap Vision)             cmH2O                8.0  
12      CPAP (Bipap Vision)             cmH2O                8.0

Quantity is there, but dose is not there, for drug exposure. I am unsure mg/ 24 hours unit meaning?  

In [207]:
%%bigquery test --project esicmdatathon2026
select * --person_id, drug_exposure_start_datetime, drug_exposure_end_datetime, drug_concept_id, quantity
from drug_exposure
where drug_concept_id in (1736887 -- linezolid
                      ,1709170    -- Meropenem
                      ,1707687    -- vancomycin
                      ,1742253    -- Levofloxacin
                      ,1778162    -- Cefuroxim
                      ,1707164    -- Metronidazol
                      ,1777806    -- Ceftriaxone
                      ,1718054    -- Caspofungin
                      ,1754994    -- Fluconazole
                      ,997881     -- Clindamycin
                      )
      and person_id = 56647 -- testing only
  limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [208]:
test

person_id  drug_concept_id drug_exposure_start_date  \
0       56647          1777806               2016-12-30   
1       56647          1742253               2017-01-08   
2       56647          1742253               2017-01-09   
3       56647          1742253               2017-01-09   
4       56647          1742253               2017-01-10   
..        ...              ...                      ...   
72      56647          1707687               2017-01-10   
73      56647          1709170               2017-01-11   
74      56647          1707687               2017-01-11   
75      56647          1707687               2017-01-28   
76      56647          1707687               2017-01-29   

   drug_exposure_start_datetime drug_exposure_end_date  \
0     2016-12-30 20:25:00+00:00             2016-12-30   
1     2017-01-08 14:34:00+00:00             2017-01-08   
2     2017-01-09 00:07:00+00:00             2017-01-09   
3     2017-01-09 11:55:00+00:00             2017-01-09   
4     2017-01-10 00:54:00+00:00             2017-01-10   
..                          ...                    ...   
72    2017-01-10 22:02:00+00:00             2017-01-10   
73    2017-01-11 10:07:00+00:00             2017-01-11   
74    2017-01-11 04:33:00+00:00             2017-01-11   
75    2017-01-28 05:21:00+00:00             2017-01-28   
76    2017-01-29 22:55:00+00:00             2017-01-29   

   drug_exposure_end_datetime  drug_type_concept_id  quantity  \
0   2016-12-30 20:25:00+00:00              38000180    2000.0   
1   2017-01-08 14:34:00+00:00              38000180     500.0   
2   2017-01-09 00:07:00+00:00              38000180     125.0   
3   2017-01-09 11:55:00+00:00              38000180     125.0   
4   2017-01-10 00:54:00+00:00              38000180     500.0   
..                        ...                   ...       ...   
72  2017-01-10 22:02:00+00:00              38000180     300.0   
73  2017-01-11 10:07:00+00:00              38000180    1000.0   
74  2017-01-11 04:33:00+00:00              38000180    1000.0   
75  2017-01-28 05:21:00+00:00              38000180    1000.0   
76  2017-01-29 22:55:00+00:00              38000180    1000.0   

                                    drug_source_value route_source_value  \
0                       CEFTRIAXON 100 MG/ML INJECTIE        intraveneus   
1                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
2                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
3                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
4                     LEVOFLOXACINE KORTLOPEND INFUUS        intraveneus   
..                                                ...                ...   
72  VANCOMYCINE INFUUS >250 MG EN <=500 MG IN NACL...        intraveneus   
73         MEROPENEM KORTLOPEND INFUUS IN NACL (VUMC)        intraveneus   
74  VANCOMYCINE INFUUS >500 MG EN <=1250 MG IN NAC...        intraveneus   
75  VANCOMYCINE INFUUS >500 MG EN <=1250 MG IN NAC...        intraveneus   
76  VANCOMYCINE INFUUS >500 MG EN <=1250 MG IN NAC...        intraveneus   

   dose_unit_source_value  
0                      mg  
1                      mg  
2                      mg  
3                      mg  
4                      mg  
..                    ...  
72                     mg  
73                     mg  
74                     mg  
75                     mg  
76                     mg  

[77 rows x 11 columns]

Blood labs are in measurements as well.

In [209]:
%%bigquery test --project esicmdatathon2026
select *
FROM measurement m
  WHERE
    measurement_concept_id in (3018405, 3047181, 3028271, 3005949, 3008037) -- searching for lactate
   and m.person_id = 56647 -- testing purpose, random visit
  limit 100


Query is running:   0%|          |

Downloading:   0%|          |

In [210]:
test


person_id  measurement_concept_id measurement_date  \
0       56647                 3008037       2017-02-10   
1       56647                 3008037       2017-02-15   
2       56647                 3008037       2017-02-16   
3       56647                 3008037       2017-01-07   
4       56647                 3008037       2016-12-31   
..        ...                     ...              ...   
95      56647                 3018405       2017-01-11   
96      56647                 3018405       2017-01-12   
97      56647                 3018405       2017-01-12   
98      56647                 3018405       2017-01-12   
99      56647                 3018405       2017-01-12   

        measurement_datetime  measurement_type_concept_id  value_as_number  \
0  2017-02-10 23:00:00+00:00                            0              1.1   
1  2017-02-15 23:00:00+00:00                            0              1.5   
2  2017-02-16 23:00:00+00:00                            0              1.9   
3  2017-01-07 06:46:00+00:00                            0              1.6   
4  2016-12-31 11:49:00+00:00                            0              2.1   
..                       ...                          ...              ...   
95 2017-01-11 02:32:00+00:00                            0              2.2   
96 2017-01-12 14:13:00+00:00                            0              1.1   
97 2017-01-12 07:18:00+00:00                            0              1.1   
98 2017-01-12 19:08:00+00:00                            0              1.2   
99 2017-01-12 04:01:00+00:00                            0              1.2   

                            measurement_source_value unit_source_value  \
0      BLOEDGAS VOLLEDIG IC PAKKET;LACTAAT VEN. VUMC            mmol/L   
1      BLOEDGAS VOLLEDIG IC PAKKET;LACTAAT VEN. VUMC            mmol/L   
2      BLOEDGAS VOLLEDIG IC PAKKET;LACTAAT VEN. VUMC            mmol/L   
3   LACTAAT (BLOEDGAS);LACTAAT - BLOEDGAS VEN. (AMC)            mmol/L   
4   LACTAAT (BLOEDGAS);LACTAAT - BLOEDGAS VEN. (AMC)            mmol/L   
..                                               ...               ...   
95                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
96                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
97                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
98                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   
99                    LACTAAT POCT;LACTAAT ART. VUMC            mmol/L   

   value_source_value  
0                 1.1  
1                 1.5  
2                 1.9  
3                 1.6  
4                 2.1  
..                ...  
95                2.2  
96                1.1  
97                1.1  
98                1.2  
99                1.2  

[100 rows x 9 columns]

Visits do not have admission from and discharged to

In [211]:
%%bigquery test --project esicmdatathon2026
select *
FROM visit_occurrence m
where person_id = 56647 -- testing purpose, random visit
  -- and admitted_from_source_value is not null
  limit 100

Query is running:   0%|          |

Downloading:   0%|          |

In [212]:
test

visit_occurrence_id  person_id  visit_concept_id visit_start_date  \
0                25373      56647              9201       2017-01-01   
1                12474      56647              9201       2017-01-07   
2                72438      56647              9201       2017-01-10   
3                45162      56647              9201       2017-02-11   

       visit_start_datetime visit_end_date        visit_end_datetime  \
0 2017-01-01 00:00:00+00:00     2017-01-07 2017-01-07 01:26:00+00:00   
1 2017-01-07 11:19:00+00:00     2017-01-10 2017-01-10 06:07:00+00:00   
2 2017-01-10 06:53:00+00:00     2017-02-10 2017-02-10 05:15:00+00:00   
3 2017-02-11 03:45:00+00:00     2017-02-15 2017-02-15 04:34:00+00:00   

   visit_type_concept_id visit_source_value  admitted_from_concept_id  \
0                  32827                icu                         0   
1                  32827                icu                         0   
2                  32827                icu                         0   
3                  32827                icu                         0   

   discharged_to_concept_id admitted_from_source_value  \
0                         0                       None   
1                         0                       None   
2                         0                       None   
3                         0                       None   

  discharged_to_source_value  
0                       None  
1                       None  
2                       None  
3                       None

A person can have multiple visits. The tracheostomy was first found in the second visit in this example.

In [213]:
%%bigquery test --project esicmdatathon2026
select d.person_id, visit_start_datetime, visit_end_datetime, min(measurement_datetime) as insert_trach
, timestamp_diff( min(measurement_datetime), min(visit_start_datetime),  hour)/24.0 as days_admit_to_first_trach
  from measurement d
inner join visit_occurrence v on d.person_id = v.person_id
       --   and timestamp_diff(v.visit_end_datetime, v.visit_start_datetime, hour )/24.0 >= 2 -- filter for longer patients only
where d.measurement_concept_id in ( 36305611  -- Tracheostomy tube diameter
        )
  and d.person_id = 56647
group by d.person_id, visit_start_datetime, visit_end_datetime


Query is running:   0%|          |

Downloading:   0%|          |

In [214]:
test

person_id      visit_start_datetime        visit_end_datetime  \
0      56647 2017-01-01 00:00:00+00:00 2017-01-07 01:26:00+00:00   
1      56647 2017-01-07 11:19:00+00:00 2017-01-10 06:07:00+00:00   
2      56647 2017-01-10 06:53:00+00:00 2017-02-10 05:15:00+00:00   
3      56647 2017-02-11 03:45:00+00:00 2017-02-15 04:34:00+00:00   

               insert_trach  days_admit_to_first_trach  
0 2017-01-09 13:34:00+00:00                   8.541667  
1 2017-01-09 13:34:00+00:00                   2.083333  
2 2017-01-09 13:34:00+00:00                  -0.708333  
3 2017-01-09 13:34:00+00:00                 -32.583333

# Now to get something working together

find all deteriorations?



Find all patients whose admissions were longer than 2 days


In [219]:
%%bigquery patientsmorethan2days --project esicmdatathon2026
select person_id, count(visit_occurrence_id) as visits
, sum(timestamp_diff( visit_end_datetime, visit_start_datetime, hour)/24.0) as sumdays
from visit_occurrence
--where person_id = 51316 -- testing purpose only
group by person_id
having sumdays > 2

Query is running:   0%|          |

Downloading:   0%|          |

In [220]:
patientsmorethan2days

person_id  visits    sumdays
0          45573       6  19.291667
1          49027       7  17.791667
2          31662       6  44.041667
3          27170       7  43.083333
4          52279       7  25.958333
...          ...     ...        ...
28011      47904       5  32.416667
28012       6121       5  44.291667
28013      38218       5  37.166667
28014      62823       5  93.708333
28015      41137       5  75.666667

[28016 rows x 3 columns]

Get conditions of these patients


In [221]:
%%bigquery conditions_list --project esicmdatathon2026
with patientsmorethan2days as
( select person_id, sum(timestamp_diff( visit_end_datetime, visit_start_datetime, hour)/24.0) as sumdays
from visit_occurrence
--where person_id = 51316 -- testing purpose only
group by person_id
having sumdays > 2 )
select c.condition_source_value, count(distinct c.person_id) as countpersons
  , avg(sumdays) as averagestay
from condition_occurrence c inner join patientsmorethan2days p
on c.person_id = p.person_id
--where c.person_id = 51316 -- testing purpose only
group by c.condition_source_value
order by count(distinct c.person_id) desc
limit 20

Query is running:   0%|          |

Downloading:   0%|          |

In [222]:
conditions_list

condition_source_value  countpersons  \
0   Cardiac arrest (with or without respiratory ar...          1321   
1           Chronic cardiovascular disease - Surgical          1204   
2         CABG alone, coronary artery bypass grafting          1126   
3                      Heart valve surgery - Surgical          1085   
4                       Non-operatief Cardiovasculair           978   
5                         Respiratory- medical, other           974   
6                        Non-operative cardiovascular           945   
7                           Operatief Cardiovasculair           930   
8                                     Diagnose anders           904   
9                                    Pneumonia, viral           899   
10                           Infection - Non surgical           888   
11                      Post-operative cardiovascular           844   
12                Aortic valve replacement (isolated)           796   
13                         Respiratory - Non surgical           750   
14                          Non-operatief Respiratoir           743   
15                               Pneumonia, bacterial           741   
16                                      Na reanimatie           726   
17                          Non-operative respiratory           683   
18    After cardiac arrest - surgical Ã« Non surgical           635   
19  Craniotomy for intracerebral subdural or subar...           601   

    averagestay  
0      8.489414  
1      6.693596  
2      5.818560  
3      7.582905  
4     11.060535  
5     18.715021  
6     10.946524  
7      8.449009  
8     20.033758  
9     15.939336  
10    17.963367  
11     8.043580  
12     5.930770  
13    19.777712  
14    15.961704  
15    15.794634  
16    14.231844  
17    16.316852  
18     8.552180  
19     9.861938

In [223]:
%%bigquery conditions_list --project esicmdatathon2026
with patientsmorethan2days as
( select person_id, sum(timestamp_diff( visit_end_datetime, visit_start_datetime, hour)/24.0) as sumdays
from visit_occurrence
--where person_id = 51316 -- testing purpose only
group by person_id
having sumdays > 2 )
select c.condition_source_value, count(distinct c.person_id) as countpersons
  , avg(sumdays) as averagestay
from condition_occurrence c inner join patientsmorethan2days p
on c.person_id = p.person_id
--where c.person_id = 51316 -- testing purpose only
group by c.condition_source_value
order by avg(sumdays)  desc
limit 20

Query is running:   0%|          |

Downloading:   0%|          |

In [224]:
conditions_list

condition_source_value  countpersons  \
0   Non-operative neurologic - Guillian-Barre synd...             5   
1   Non-operative cardiovascular - Cardiovascular ...            18   
2   Post-operative respiratory - Thoracotomy for b...             3   
3   Post-operative cardiovascular - Grafts, all ot...             6   
4   Post-operative neurologic - Seizures-intractab...             4   
5      Non-operative Gastro-intestinal - Pancreatitis            19   
6      Non-operative respiratory - Effusions, pleural            33   
7   Non-operative musculo-skeletal - Cellulitis an...             8   
8                             Cholangitis/Pancratitis            39   
9   Post-operative trauma - Chest/spinal trauma, s...             4   
10  Non-operative genitourinary - Renal neoplasm, ...             1   
11   Operatief Cardiovasculair - Haemorragische shock            31   
12  Post-operative gastro-intestinal - Cancer-smal...             3   
13                         Ontlasting pericardeffusie            19   
14   Non-operative cardiovascular - Sepsis, pulmonary            49   
15  Non-operative respiratory - Pneumonia, aspiration            70   
16  Non-operative genitourinary - Renal infection/...            16   
17  Post-operative cardiovascular - Pericardial ef...            10   
18  Post-operative hematology - Hematologic surger...             1   
19            Trauma wervelfr/dwarslaesie (operatief)            14   

    averagestay  
0     84.319039  
1     71.404000  
2     65.073551  
3     60.643519  
4     56.350340  
5     54.729347  
6     54.051144  
7     52.202140  
8     51.830900  
9     51.715054  
10    47.000000  
11    46.872636  
12    46.805894  
13    46.327441  
14    46.116240  
15    46.006634  
16    45.025768  
17    43.998756  
18    43.750000  
19    43.480208